# **Bitcoin price prediction - Final scores**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author: Corsi Danilo (1742375) - corsi.1742375@studenti.uniroma1.it


---


Description: testing the final models and compare the results.

# Global constants, dependencies, libraries and tools

In [2]:
# Main constants
LOCAL_RUNNING = True
ROOT_DIR = "D:/Documents/Repository/BDC/project" if LOCAL_RUNNING else "/content/drive"

In [3]:
if not LOCAL_RUNNING:
    # Point Colaboratory to Google Drive
    from google.colab import drive

    # Define GDrive paths
    drive.mount(ROOT_DIR, force_remount=True)

    # Install Spark and related dependencies
    !pip install pyspark
    !pip install -U -q PyDrive -qq
    !apt install openjdk-8-jdk-headless -qq

    # Install "kaleido" engine package to export image
    !pip install -U kaleido

## Import my utilities

In [4]:
# Set main dir
MAIN_DIR = ROOT_DIR + "" if LOCAL_RUNNING else ROOT_DIR + "/MyDrive/BDC/project"

# Utilities dir
UTILITIES_DIR = MAIN_DIR + "/utilities"

# Import my utilities
import sys
sys.path.append(UTILITIES_DIR)

from imports import *
from config import *
import final_scores_utilities

importlib.reload(final_scores_utilities)

<module 'final_scores_utilities' from 'D:\\Documents/Repository/BDC/project/utilities\\final_scores_utilities.py'>

In [5]:
# Set main dir
MAIN_DIR = ROOT_DIR + "" if LOCAL_RUNNING else ROOT_DIR + "/MyDrive/BDC/project"

###################
# --- DATASET --- #
###################

# Datasets dirs
DATASET_OUTPUT_DIR = MAIN_DIR + "/datasets/output"

# Datasets paths
DATASET_TEST = DATASET_OUTPUT_DIR + "/" + DATASET_TEST_NAME + ".parquet"

####################
# --- FEATURES --- #
####################

# Features dir
FEATURES_DIR = MAIN_DIR + "/features"

# Features paths
FEATURES_CORRELATION = FEATURES_DIR + "/" + FEATURES_CORRELATION_LABEL + ".json"
BASE_FEATURES = FEATURES_DIR + "/" + BASE_FEATURES_LABEL + ".json"
BASE_AND_MOST_CORR_FEATURES = FEATURES_DIR + "/" + BASE_AND_MOST_CORR_FEATURES_LABEL + ".json"
BASE_AND_LEAST_CORR_FEATURES = FEATURES_DIR + "/" + BASE_AND_LEAST_CORR_FEATURES_LABEL + ".json"

##################
# --- MODELS --- #
##################

# Model dir
MODELS_DIR = MAIN_DIR + "/models"

# Model path
LR_MODEL = MODELS_DIR + "/" + LR_MODEL_NAME
GLR_MODEL = MODELS_DIR + "/" + GLR_MODEL_NAME
RF_MODEL = MODELS_DIR + "/" + RF_MODEL_NAME
GBTR_MODEL = MODELS_DIR + "/" + GBTR_MODEL_NAME

###################
# --- RESULTS --- #
###################

# Results dir
RESULTS_DIR = MAIN_DIR + "/results"
RESULTS_FINAL_DIR = RESULTS_DIR + "/final"

In [6]:
# Suppression of warnings for better reading
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

pio.renderers.default = 'vscode+colab' # To correctly render plotly plots

# Create the pyspark session

In [6]:
# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '12G').\
                set('spark.driver.memory', '12G').\
                set('spark.driver.maxResultSize', '109G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPricePrediction").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

# Loading dataset

In [7]:
# Load datasets into pyspark dataset objects
df = spark.read.load(DATASET_TEST,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

In [8]:
final_scores_utilities.dataset_info(df)

+-------------------+------+------------+------------------+------------------+------------------+------------------+------------------+--------------------+--------------------+--------------------+------------------+------------------+--------------------+------------------------+--------------------+------------------+--------------------+--------------------+------------------+-----------------+--------------------------------+------------------+------------------+------------------+------------------+------------------+------------------+-----------------+
|          timestamp|    id|market-price|     opening-price|     highest-price|      lowest-price|     closing-price|  trade-volume-btc|      total-bitcoins|          market-cap|    trade-volume-usd|       blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|           hash-rate|        difficulty|      miners-revenue|transaction-fees-usd|n-unique-addresses|   n-transactions|estimated-transaction-volume-u

# Compare train / validation results

In [9]:
splits_list = [BLOCK_SPLITS_NAME, WALK_FORWARD_SPLITS_NAME, SHORT_TERM_SPLITS_NAME]
models_list = [LR_MODEL_NAME, GLR_MODEL_NAME, RF_MODEL_NAME, GBTR_MODEL_NAME]

In [10]:
# Load all results
train_valid_all_results_raw = final_scores_utilities.get_all_results(splits_list, models_list, RESULTS_DIR) # Get all results

In [11]:
train_valid_all_results = train_valid_all_results_raw[train_valid_all_results_raw['Dataset'] != 'train'].copy() # Remove the 'train' dataset

train_valid_all_results = final_scores_utilities.train_valid_dataset_fine_tuning(train_valid_all_results, 'results') # Fine tuning of the dataset
train_valid_all_results = train_valid_all_results[(train_valid_all_results['Dataset'] == 'valid') & (train_valid_all_results['Type'] == 'Default')] # Get only the default results

## RMSE and R2 values compared with the features used in the default models

In [12]:
rmse_title = 'RMSE per Features type'
r2_title = 'R2 per Features type'
save_path = RESULTS_FINAL_DIR + "/plots/default_"
final_scores_utilities.train_val_rmse_r2_plot(train_valid_all_results, 'Features', 'Model', 'RMSE', 'R2', 'Splitting', rmse_title, r2_title, save_path)

In [13]:
# Exclude negative R2 values
train_valid_all_results_non_negative = train_valid_all_results[train_valid_all_results['R2'] >= 0].copy()

# # Convert the columns to a category type with the custom order
train_valid_all_results_non_negative['Features'] = pd.Categorical(train_valid_all_results_non_negative['Features'], categories=final_scores_utilities.features_order, ordered=True)
train_valid_all_results_non_negative['Splitting'] = pd.Categorical(train_valid_all_results_non_negative['Splitting'], categories=final_scores_utilities.splitting_order, ordered=True)

# Sort the DataFrame by the columns
train_valid_all_results_non_negative.sort_values(by=['Features', 'Splitting'], inplace=True)

r2_title = 'R2 per Model type (non-negative)'
final_scores_utilities.train_val_r2_plot(train_valid_all_results_non_negative, 'Features', 'Model', 'R2', 'Splitting', r2_title)

Considering the RMSE and R2 value of each default model according to the splitting method, we can see that, in general, the normalized features are the ones that returned the worst results giving a very high RMSE value. In particular, we have some cases where R2 has very low and high values, in fact, although they helped to reduce overfitting in some cases (such as in the case of LR and GLR where for non-normalised features we had an R2 close to 1) in others they made the situation worse (such as in the case of LR and GLR where for normalized features we had a negative R2 value).

Regarding the groups of features chosen, we can say that mainly, depending on the type of model, these were more or less useful (e.g. for linear models it is preferable to use the normalized ones while for tree-based models it is not). The addition of the blockchain features would seem to have made a slight improvement in some cases (this indicates that the price-based features still carry weight).

In conclusion, the features used to train each model are:

- **LR**: Base + most corr. features (with normalization)
- **GLR**: Base + most corr. features (with normalization)
- **RF**: Base features (without normalization)
- **GBTR**: Base + least corr. features (without normalization)

In [14]:
# Load relevant results
train_valid_results_raw, train_valid_accuracy_raw = final_scores_utilities.get_rel_results(splits_list, models_list, RESULTS_DIR) # Get relevant results

train_valid_results = final_scores_utilities.train_valid_dataset_fine_tuning(train_valid_results_raw.copy(), 'results') # Fine tuning of the dataset
train_valid_accuracy = final_scores_utilities.train_valid_dataset_fine_tuning(train_valid_accuracy_raw.copy(), 'accuracy') # Fine tuning of the dataset

In [15]:
train_valid_results = final_scores_utilities.train_valid_dataset_fine_tuning(train_valid_results, 'results')
train_valid_results

Model     Type Dataset            Splitting  \
0     LR  Default   valid         Block splits   
1     LR    Tuned   valid         Block splits   
2    GLR  Default   valid         Block splits   
3    GLR    Tuned   valid         Block splits   
4     RF  Default   valid         Block splits   
5     RF    Tuned   valid         Block splits   
6   GBTR  Default   valid         Block splits   
7   GBTR    Tuned   valid         Block splits   
8     LR  Default   valid  Walk-forward splits   
9     LR    Tuned   valid  Walk-forward splits   
10   GLR  Default   valid  Walk-forward splits   
11   GLR    Tuned   valid  Walk-forward splits   
12    RF  Default   valid  Walk-forward splits   
13    RF    Tuned   valid  Walk-forward splits   
14  GBTR  Default   valid  Walk-forward splits   
15  GBTR    Tuned   valid  Walk-forward splits   
16    LR  Default   valid         Single split   
17    LR    Tuned   valid         Single split   
18   GLR  Default   valid         Single split   
19   GLR    Tuned   valid         Single split   
20    RF  Default   valid         Single split   
21    RF    Tuned   valid         Single split   
22  GBTR  Default   valid         Single split   
23  GBTR    Tuned   valid         Single split   

                               Features                   Parameters  \
0   Base + least corr. features (norm.)              [100, 0.0, 0.0]   
1   Base + least corr. features (norm.)                [5, 0.8, 0.0]   
2   Base + least corr. features (norm.)                      [25, 0]   
3   Base + least corr. features (norm.)  [5, 0.1, 'gaussian', 'log']   
4                         Base features                  [20, 5, 42]   
5                         Base features                 [30, 10, 42]   
6                         Base features             [20, 5, 0.1, 42]   
7                         Base features              [3, 5, 0.1, 42]   
8   Base + least corr. features (norm.)              [100, 0.0, 0.0]   
9                 Base features (norm.)                [5, 0.0, 0.0]   
10  Base + least corr. features (norm.)                      [25, 0]   
11                Base features (norm.)  [5, 0.1, 'gaussian', 'log']   
12                        Base features                  [20, 5, 42]   
13                        Base features                 [10, 10, 42]   
14                        Base features             [20, 5, 0.1, 42]   
15                        Base features             [20, 3, 0.7, 42]   
16   Base + most corr. features (norm.)              [100, 0.0, 0.0]   
17   Base + most corr. features (norm.)              [100, 0.4, 0.4]   
18   Base + most corr. features (norm.)                      [25, 0]   
19   Base + most corr. features (norm.)  [5, 0.2, 'gaussian', 'log']   
20                        Base features                  [20, 5, 42]   
21                        Base features                  [5, 10, 42]   
22          Base + least corr. features             [20, 5, 0.1, 42]   
23          Base + least corr. features              [3, 5, 0.3, 42]   

           RMSE           MSE          MAE      MAPE        R2  Adjusted_R2  \
0   2227.412278  8.171259e+06  1870.345923  0.052480 -1.631054    -1.633063   
1   1032.704613  1.732495e+06   776.557626  0.022809  0.583006     0.582688   
2   2227.412278  8.171259e+06  1870.345923  0.052480 -1.631054    -1.633063   
3   1613.055150  4.358777e+06  1318.116337  0.036782  0.253175     0.252605   
4    874.913453  8.768811e+05   579.679197  0.022112  0.337898     0.337393   
5    772.597736  7.135922e+05   497.460229  0.018699  0.530111     0.529753   
6    694.841380  6.411613e+05   446.415138  0.016936  0.763292     0.763111   
7    732.282155  7.287943e+05   478.257071  0.018009  0.735400     0.735198   
8   1743.625346  5.340021e+06  1496.804362  0.043785  0.360428     0.359915   
9   1664.415862  4.874436e+06  1430.474180  0.041731  0.435987     0.435535   
10  1743.625346  5.340021e+06  1496.804362  0.043785  0.360428     0.359915   
11 

In [16]:
train_valid_accuracy = final_scores_utilities.train_valid_dataset_fine_tuning(train_valid_accuracy, 'accuracy')
train_valid_accuracy

Model                             Features            Splitting  \
0     LR  Base + least corr. features (norm.)         Block splits   
1    GLR  Base + least corr. features (norm.)         Block splits   
2     RF                        Base features         Block splits   
3   GBTR                        Base features         Block splits   
4     LR                Base features (norm.)  Walk-forward splits   
5    GLR                Base features (norm.)  Walk-forward splits   
6     RF                        Base features  Walk-forward splits   
7   GBTR                        Base features  Walk-forward splits   
8     LR   Base + most corr. features (norm.)         Single split   
9    GLR   Base + most corr. features (norm.)         Single split   
10    RF                        Base features         Single split   
11  GBTR          Base + least corr. features         Single split   

    Accuracy (default)  Accuracy (tuned)  
0            48.211971         46.164697  
1            48.211971         48.215783  
2            53.808616         54.292795  
3            51.044605         50.171559  
4            48.015455         50.306364  
5            48.015455         47.985455  
6            50.989091         51.544545  
7            49.032727         50.008182  
8            46.706989         50.268817  
9            46.706989         46.673387  
10           49.663978         46.875000  
11           54.536290         55.779570

## RMSE and R2 values compared between default and tuned models

In [17]:
rmse_title = 'RMSE per Model type'
r2_title = 'R2 per Model type'
save_path = RESULTS_FINAL_DIR + "/plots/final_"
final_scores_utilities.train_val_rmse_r2_plot(train_valid_results, 'Type', 'Model', 'RMSE', 'R2', 'Splitting', rmse_title, r2_title, save_path)

In [18]:
# Exclude negative R2 values
train_valid_results_non_negative = train_valid_results[train_valid_results['R2'] >= 0].copy()

# # Convert the columns to a category type with the custom order
train_valid_results_non_negative['Type'] = pd.Categorical(train_valid_results_non_negative['Type'], categories=final_scores_utilities.type_order, ordered=True)
train_valid_results_non_negative['Model'] = pd.Categorical(train_valid_results_non_negative['Model'], categories=final_scores_utilities.model_order, ordered=True)
train_valid_results_non_negative['Splitting'] = pd.Categorical(train_valid_results_non_negative['Splitting'], categories=final_scores_utilities.splitting_order, ordered=True)

# Sort the DataFrame by the columns
train_valid_results_non_negative.sort_values(by=['Splitting', 'Type', 'Model'], inplace=True)

r2_title = 'R2 per Model type (non-negative)'
final_scores_utilities.train_val_r2_plot(train_valid_results_non_negative, 'Type', 'Model', 'R2', 'Splitting', r2_title)

Here we have a comparison of the best default model and the model after hyperparameter tuning. We can see that the trend regarding splitting methods has remained the same, i.e. single split is the best method on which to train / validate the models. In general, hyperparameter tuning brought some improvements in the tuned model compared with the results obtained with the default models.

## Accuracy percentage compared between default and tuned models

In [19]:
# Group by 'Splitting'
train_valid_accuracy_grouped = train_valid_accuracy.groupby('Splitting')

title = 'Percentage of accuracy between default and tuned model'
save_path = RESULTS_FINAL_DIR + "/plots/final_"
final_scores_utilities.train_val_accuracy_plot(train_valid_accuracy_grouped, 'Model', 'Accuracy (default)', 'Accuracy (tuned)', title, save_path)

Looking at accuracy, on the other hand, we can see that this has remained more or less the same among all splitting methods.

In conclusion, we can say that the splitting method that performed best was the single split, probably due to the shorter period taken into account, and the models that returned the best results were the tree-based models.

# Test models
After loading the trained models, the test set is divided into further mini-sets of `1 week`, `15 days`, `1 month` and `3 months` to see how the models' performance degrades as time increases. Final results are collected and compared to draw conclusions (see final results).

In [20]:
# Retrieve the last value of the timestamp column
first_timestamp = df.select(col("timestamp")).first()[0]

# Split the test set into mini-sets of 1 week, 15 days, 1 month, and 3 months
one_week_df = df.filter(col("timestamp") <= first_timestamp + relativedelta(weeks=1))
fifteen_days_df = df.filter(col("timestamp") <= first_timestamp + relativedelta(days=15))
one_month_df = df.filter(col("timestamp") <= first_timestamp + relativedelta(months=1))
three_months_df = df.filter(col("timestamp") <= first_timestamp + relativedelta(months=3))

# Save datasets
datasets_list = [one_week_df, fifteen_days_df, one_month_df, three_months_df]

In [21]:
final_scores_utilities.show_datasets(one_week_df.toPandas(), fifteen_days_df.toPandas(), one_month_df.toPandas(), three_months_df.toPandas(), "Test set split")

In this graph each split is overlaid with the others, to view them individually turn on / off the elements in the legend.

In [22]:
# Loading base features
with open(BASE_FEATURES, "r") as f:
    BASE_FEATURES = json.load(f)
print(BASE_FEATURES)

['opening-price', 'highest-price', 'lowest-price', 'closing-price', 'trade-volume-btc', 'market-price', 'market-cap', 'total-bitcoins', 'trade-volume-usd']


In [23]:
# Loading currency and additional most correlated features
with open(BASE_AND_MOST_CORR_FEATURES, "r") as f:
    BASE_AND_MOST_CORR_FEATURES = json.load(f)
print(BASE_AND_MOST_CORR_FEATURES)

['opening-price', 'highest-price', 'lowest-price', 'closing-price', 'trade-volume-btc', 'market-price', 'market-cap', 'total-bitcoins', 'trade-volume-usd', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'estimated-transaction-volume-usd', 'sma-20-days']


In [24]:
# Loading currency and additional least correlated features
with open(BASE_AND_LEAST_CORR_FEATURES, "r") as f:
    BASE_AND_LEAST_CORR_FEATURES = json.load(f)
print(BASE_AND_LEAST_CORR_FEATURES)

['opening-price', 'highest-price', 'lowest-price', 'closing-price', 'trade-volume-btc', 'market-price', 'market-cap', 'total-bitcoins', 'trade-volume-usd', 'sma-100-days', 'transaction-fees-usd', 'n-unique-addresses', 'sma-50-days', 'n-transactions-total', 'blocks-size', 'hash-rate', 'difficulty', 'avg-block-size', 'n-transactions-per-block', 'n-transactions']


In [25]:
# Load models
lr = PipelineModel.load(LR_MODEL)
glr = PipelineModel.load(GLR_MODEL)
rf = PipelineModel.load(RF_MODEL)
gbtr = PipelineModel.load(GBTR_MODEL)

In [26]:
# Group models and features
features_list = [BASE_FEATURES, BASE_AND_MOST_CORR_FEATURES, BASE_AND_LEAST_CORR_FEATURES]
models_list = [lr, glr, rf, gbtr]

# Get model parameters
model_params_list = final_scores_utilities.get_model_parameters(train_valid_results_raw, models_list, features_list)
print(model_params_list)

[{'Model_name': 'LinearRegression', 'Model': PipelineModel_7a5576eee5dd, 'Features_label': 'base_and_most_corr_features_norm', 'Features': ['opening-price', 'highest-price', 'lowest-price', 'closing-price', 'trade-volume-btc', 'market-price', 'market-cap', 'total-bitcoins', 'trade-volume-usd', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'estimated-transaction-volume-usd', 'sma-20-days'], 'Normalization': True}, {'Model_name': 'GeneralizedLinearRegression', 'Model': PipelineModel_c128882cd8e7, 'Features_label': 'base_and_most_corr_features_norm', 'Features': ['opening-price', 'highest-price', 'lowest-price', 'closing-price', 'trade-volume-btc', 'market-price', 'market-cap', 'total-bitcoins', 'trade-volume-usd', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'estimated-transaction-volume-usd', 'sma-20-days'], 'Normalization': True}, {'Model_name': 'RandomForestRegressor', 'Model': PipelineModel_2a89489a9eb0, 'Features_label': 'base_features', 'Features': ['

In [27]:
final_test_results_raw, predictions_df = final_scores_utilities.models_testing(datasets_list, model_params_list)

# Final results

In [28]:
final_test_results = final_scores_utilities.test_dataset_fine_tuning(final_test_results_raw.copy())
final_test_results

Model       Dataset                            Features         RMSE  \
0     LR      One week  Base + most corr. features (norm.)  2609.393648   
1     LR  Fifteen days  Base + most corr. features (norm.)  2946.197227   
2     LR     One month  Base + most corr. features (norm.)  3088.128452   
3     LR  Three months  Base + most corr. features (norm.)  2282.902299   
4    GLR      One week  Base + most corr. features (norm.)  2987.628423   
5    GLR  Fifteen days  Base + most corr. features (norm.)  3423.588091   
6    GLR     One month  Base + most corr. features (norm.)  3564.472652   
7    GLR  Three months  Base + most corr. features (norm.)  2579.296794   
8     RF      One week                       Base features   513.337110   
9     RF  Fifteen days                       Base features   800.702651   
10    RF     One month                       Base features   980.347060   
11    RF  Three months                       Base features  1846.604162   
12  GBTR      One week         Base + least corr. features   192.482113   
13  GBTR  Fifteen days         Base + least corr. features   158.135901   
14  GBTR     One month         Base + least corr. features   357.665880   
15  GBTR  Three months         Base + least corr. features  2264.889058   

             MSE          MAE      MAPE        R2  Adjusted_R2   Accuracy  
0   6.808935e+06  2440.497200  0.088330 -2.663772    -2.685711  71.322437  
1   8.680078e+06  2846.512298  0.106555 -3.630695    -3.643594  66.620402  
2   9.536537e+06  2995.746203  0.113862 -6.276874    -6.286668  64.494458  
3   5.211643e+06  2027.938757  0.072343  0.580316     0.580126  57.835145  
4   8.925924e+06  2804.728440  0.101492 -3.802888    -3.831648  71.322437  
5   1.172096e+07  3312.875054  0.124036 -5.252958    -5.270376  66.620402  
6   1.270547e+07  3476.982746  0.132117 -8.694931    -8.707979  64.494458  
7   6.652772e+06  2262.833504  0.080586  0.464265     0.464022  56.985960  
8   2.635150e+05   365.313231  0.013612  0.858207     0.857358  53.640416  
9   6.411247e+05   690.581401  0.026253  0.657969     0.657017  45.038168  
10  9.610804e+05   885.791341  0.033961  0.266646     0.265659  41.148808  
11  3.409947e+06  1317.215560  0.042419  0.725403     0.725279  45.210598  
12  3.704936e+04   165.455458  0.005905  0.980064     0.979945  67.161961  
13  2.500696e+04   133.985589  0.004929  0.986659     0.986622  53.296322  
14  1.279249e+05   256.939135  0.009813  0.902387     0.902255  47.329526  
15  5.129722e+06  1197.481513  0.035548  0.586913     0.586726  48.573370

## Prediction

In [29]:
datasets_name_raw_list = ["one_week", "fifteen_days", "one_month", "three_months"]

# For each dataset type, it displays the predicitons of each model
for i, data in enumerate(datasets_list):
    predictions_to_show = predictions_df[predictions_df['Dataset'] == datasets_name_raw_list[i]]

    lr_predictions = predictions_to_show[predictions_to_show['Model'] == LR_MODEL_NAME]
    glr_predictions = predictions_to_show[predictions_to_show['Model'] == GLR_MODEL_NAME]
    rf_predictions = predictions_to_show[predictions_to_show['Model'] == RF_MODEL_NAME]
    gbtr_predictions = predictions_to_show[predictions_to_show['Model'] == GBTR_MODEL_NAME]

    final_scores_utilities.show_results(
        data.toPandas(),
        final_scores_utilities.model_order[0], lr_predictions,
        final_scores_utilities.model_order[1], glr_predictions,
        final_scores_utilities.model_order[2], rf_predictions,
        final_scores_utilities.model_order[3], gbtr_predictions,
        final_scores_utilities.dataset_order[i] + " predictions")

Considering the final predictions made on the test set, we can see that, confirming what was seen in the resultrs of the train / validation phase, tree-based methods perform rather well in the short-mid term period (one week, fifteen days, one month), compared to linear methods, while in the long term period (three months), especially considering the last month, all models failed to capture the price trend well.

## RMSE and R2 values of each model for each dataset split

In [30]:
rmse_title = 'RMSE per Dataset type'
r2_title = 'R2 per Dataset type'
save_path = RESULTS_FINAL_DIR + "/plots/final_"
final_scores_utilities.test_rmse_r2_plot(final_test_results, 'Model', 'RMSE', 'R2', 'Dataset', rmse_title, r2_title, save_path)

In [31]:
# Exclude negative R2 values
final_test_results_non_negative = final_test_results[final_test_results['R2'] >= 0].copy()

# # Convert the columns to a category type with the custom order
final_test_results_non_negative['Dataset'] = pd.Categorical(final_test_results_non_negative['Dataset'], categories=final_scores_utilities.dataset_order, ordered=True)
final_test_results_non_negative['Model'] = pd.Categorical(final_test_results_non_negative['Model'], categories=final_scores_utilities.model_order, ordered=True)

# Sort the DataFrame by the columns
final_test_results_non_negative.sort_values(by=['Dataset', 'Model'], inplace=True)

r2_title = 'R2 per Dataset type (non-negative)'
final_scores_utilities.test_r2_plot(final_test_results_non_negative, 'Model', 'R2', 'Dataset', r2_title)

Considering the RMSE and R2 values we can see that the previous theory is confirmed, where in fact, especially in the long run RMSE tends to increase and R2 to decrease for both types of models. Note that by averaging all the results obtained and having more data available, we can see how the periods in which the models did better (one week, fifteen days and one month) compensated for the worst results in the last period (three months).

## Accuracy percentage of each model for each dataset split

In [32]:
# Group by 'Splitting'
final_test_results_grouped = final_test_results.groupby('Dataset')

title = 'Percentage of accuracy between default and tuned model'
save_path = RESULTS_FINAL_DIR + "/plots/final_"
final_scores_utilities.test_accuracy_plot(final_test_results_grouped, 'Model', 'Accuracy', title, save_path)

Considering the accuracy, this is slightly improved compared to that obtained during the train / validation phase, in general this is higher when we consider the short term period (one week, fifteen days) and tends to decrease in the long term period (one month, three months). It should be noted that in this case linear models have a higher accuracy than tree-based models, probably because they have smoother curves that allow them to better represent price than tree-based models that are more jagged.

In conclusion, we can say that considering a shorter period helps to get better results, and those that benefit most are tree-based methods regarding price prediction, considering accuracy, however, the linear ones seem to guess better when the price goes up or down.

# Saving final results

In [33]:
# Saving test results
final_test_results_raw.to_csv(RESULTS_FINAL_DIR + "/final.csv", index=False)

In [7]:
# Export notebook in html format (remember to save the notebook and change the model name)
if LOCAL_RUNNING:
  !jupyter nbconvert --to html 6-final-scores.ipynb --output 6-final-scores --output-dir='./exports'

d:\Documents\Repository\BDC\project\.bdc\Lib\site-packages\traitlets\traitlets.py:2548: FutureWarning: Supporting extra quotes around strings is deprecated in traitlets 5.0. You can use '../exports' instead of "'../exports'" if you require traitlets >=5.
  warn(
[NbConvertApp] Converting notebook 6-final-scores.ipynb to html
[NbConvertApp] Writing 3913978 bytes to ..\exports\6-final-scores.html
